In [1]:
#----------------- clean copy that reproduces main results from Preprocessing_Features_Model
import json 
import os 
from sklearn.utils import shuffle    
import numpy as np
import pandas as pd
from sklearn import preprocessing
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
main_dir = os.path.dirname(os.getcwd())

#### Load BTC data used in https://github.com/gdemos01/crypto-trading-ai-bot-basic

In [2]:
# Opening JSON file

#f = open(main_dir + '/data/2020_10__BTC-USD.json',)
f = open(main_dir + r'\BTC-USD\2020_10__BTC-USD.json',) 
data = json.load(f)

total = []
for i in data:
    for j in i:
        time = pd.to_datetime(j[0], unit='s')
        open_ = j[1]
        high = j[2]
        low = j[3]
        close = j[4]
        vol = j[5]
        total.append( [time, open_, high, low, close, vol])

#1601510460000

In [3]:
data

[[[1601510400, 10779.63, 10788.5, 10779.63, 10783.24, 3.50667047],
  [1601510460, 10782.98, 10799.99, 10783.24, 10796.02, 15.46159883],
  [1601510520, 10791.83, 10798.73, 10796.01, 10795.06, 17.63006328],
  [1601510580, 10793.67, 10799.99, 10795.06, 10799.99, 2.6463716],
  [1601510640, 10799.45, 10829.99, 10799.45, 10817.42, 47.83403845],
  [1601510700, 10815.13, 10825, 10815.13, 10824.16, 1.91609476],
  [1601510760, 10817.88, 10828.37, 10822.81, 10817.88, 14.50437905],
  [1601510820, 10811.73, 10818.67, 10818.67, 10815.6, 18.71285643],
  [1601510880, 10809.73, 10822.47, 10815.59, 10821.9, 6.31546161],
  [1601510940, 10816.56, 10827.39, 10822.64, 10816.56, 11.26600696],
  [1601511000, 10806.57, 10819.75, 10816.57, 10811.28, 20.70867756],
  [1601511060, 10807.61, 10812.9, 10811.28, 10808.67, 1.6799306],
  [1601511120, 10806.94, 10812.52, 10808.68, 10812.52, 2.9562904],
  [1601511180, 10807.95, 10812.93, 10810.56, 10810.84, 1.65008851],
  [1601511240, 10806.72, 10813.22, 10810.84, 10810.

In [4]:
len(data),len(data[0]),len(data[0][0]), len(data)*len(data[0])

(732, 61, 6, 44652)

In [5]:

def createTrainTestSets(coin_data, training_window = 180, labeling_window = 60, feature_window = 30):
    
    '''
    #---- WHAT DOES THIS FUNCTION MAKES EXACTLY?
    
    ARGS:
        - coin_data: minute price data array (n,m). n=total minutes, m=features.
        - training_window: how many minutes (backwards in time) we use to compute features. 
                           We use it to compute averages.
        - labeling_window: timeframe we want to label (e.g. we label every 1 hour/ 60 min)
        - feature_window: Define local window to compute accelerations.
    '''
    time_list = []
    x = []
    y = []
    prices = []

    positive = 0
    negative = 0
    block = 60  # Move 1 hour
    start_index = 0
    end_index = training_window -1

    while end_index < len(coin_data) - labeling_window - block - 1:
        features = []
        feature_names = []

        # Latest Values
        time_list.append( coin_data[end_index][0] )
        latest_low_price = coin_data[end_index][1]
        latest_high_price = coin_data[end_index][2]
        latest_open_price = coin_data[end_index][3]
        latest_close_price = coin_data[end_index][4]
        latest_volume = coin_data[end_index][5]

        #print('=========================')
        #print(coin_data[end_index][0])

        # Accelerations and Differences
        acc_index = 0
        total_window_volume = 0
        prev_window_volume_acceleration = 0
        window_volume_acceleration = 0
        average_volume_acceleration = 0 # The average volume acceleration based on the feature window (local)
        average_close_price_acceleration = 0 # The average close price acceleration based on the feature window (local)
        average_close_price_diff = 0 # The average close price difference based on the feature window (local)

        # Averages
        average_close_price = 0
        average_volume = 0

        for i in range(start_index,end_index):
            #print(i, coin_data[i][0])
            cur_close_price = coin_data[i][4]
            cur_volume = coin_data[i][5]
            total_window_volume += cur_volume
            window_volume_acceleration += cur_volume
            average_close_price += cur_close_price

            #==============================================================================================#
            # Local Accelerations
            acc_index += 1
            if acc_index % feature_window == 0:
                # Local Close Price Acceleration
                close_price_acceleration = (cur_close_price / coin_data[i-feature_window][4]) - 1
                features.append(close_price_acceleration)
                feature_names.append("close_price_acc_"+str(acc_index))
                average_close_price_acceleration += close_price_acceleration

                # Local Close Price Difference - Only overal average added in features
                close_price_diff = cur_close_price - coin_data[i-feature_window][4]
                average_close_price_diff +=  close_price_diff

                # Local Volume Acceleration
                if prev_window_volume_acceleration != 0:
                    volume_acceleration = (window_volume_acceleration / prev_window_volume_acceleration) - 1
                    features.append(volume_acceleration)
                    feature_names.append("volume_acc_"+str(acc_index))
                average_volume_acceleration += window_volume_acceleration
                prev_window_volume_acceleration = window_volume_acceleration
                window_volume_acceleration = 0
            #==============================================================================================#

        # Overall Averages
        average_close_price /= training_window
        average_close_price_acceleration /= training_window
        average_volume /= training_window
        average_volume_acceleration /= training_window

        # Price
        overall_price_difference = latest_close_price - coin_data[start_index][4]
        overall_price_acceleration = (latest_close_price / coin_data[start_index][4]) - 1

        # Adding Features and Feature Names

        # Volumen of the last training_window minutes
        features.append(total_window_volume)
        feature_names.append("volume_total")

        # Price at the minute being classified 
        features.append(latest_low_price)
        feature_names.append("low_price_latest")
        features.append(latest_high_price)
        feature_names.append("high_price_latest")
        features.append(latest_open_price)
        feature_names.append("open_price_latest")
        features.append(latest_close_price)
        feature_names.append("close_price_latest")

        # Average of close price over training_window minutes
        features.append(average_close_price)
        feature_names.append("close_price_av")

        # Accs ?
        features.append(average_close_price_acceleration)
        feature_names.append("close_price_acc_av")
        features.append(average_close_price_diff)
        feature_names.append("close_price_diff_av")
        features.append(average_volume)
        feature_names.append("volume_av")
        features.append(average_volume_acceleration)
        feature_names.append("volume_acc_av")
        features.append(overall_price_difference)
        feature_names.append("overall_price_diff")
        features.append(overall_price_acceleration)
        feature_names.append("overal_price_acc")

        # Close price at the minunte being classified (same as latest_close_price)
        prices.append(latest_close_price)

        # append features
        x.append(features) # Add to training set

        # lastest_close_price in the next labeling_window minutes 
        next_close_price = coin_data[end_index + labeling_window +1][4]

        # pct change 
        change_rate = (next_close_price/latest_close_price) - 1

        #labeling UP/DOWN
        if change_rate > 0:
            y.append(1)
            positive += 1
        else:
            y.append(0)
            negative +=1

        start_index += block
        end_index += block

    print("> Finished Creating set - Size: ",len(x)," ",len(y)," P: ",positive," N: ",negative)

    x = preprocessing.scale(x)
    time_list, x, y, prices = shuffle(time_list, x, y, prices)

    return time_list, np.array(x), np.array(y), prices

In [6]:
time_list, x, y, prices = createTrainTestSets(total, training_window = 20, labeling_window = 60, feature_window = 30)

> Finished Creating set - Size:  739   739  P:  408  N:  331


In [7]:
x, y

(array([[-0.52337881, -1.20568184, -1.20650003, ...,  0.        ,
          0.00354377,  0.01805931],
        [-0.48746747, -0.39976609, -0.40045648, ...,  0.        ,
         -0.32980222, -0.35129869],
        [-0.61637166, -0.44260524, -0.44547846, ...,  0.        ,
         -0.67610831, -0.72917736],
        ...,
        [-0.47639772, -0.337415  , -0.33497683, ...,  0.        ,
          0.29891363,  0.32943252],
        [-0.58047544, -1.11798701, -1.11883509, ...,  0.        ,
         -0.29574426, -0.33093819],
        [-0.35237701,  1.64415866,  1.63543576, ...,  0.        ,
         -0.03865192, -0.04248033]]),
 array([1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 1, 0, 1,
        0, 1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 0, 1, 1, 1, 1, 1, 1, 0, 0, 1, 0,
        0, 0, 1, 0, 1, 1, 0, 0, 1, 0, 1, 1, 1, 1, 1, 0, 1, 0, 0, 0, 1, 1,
        0, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 0, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1,
        1, 1, 0, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 0, 0, 0, 1, 1, 1, 1, 0,
   

# Lets load my BTC data and repeat this process

In [8]:
path=r'C:\Users\vicmual\Desktop\CODING\CryptoBot_Mendez\cryptobot-project'

#--- look at table and compare with second row:
#--- Open Time / Open/High/Low /Close/ Volume (not sure of this last one!)
df2=pd.read_csv(path+r'\BTC_USD_1month_features.csv' )
df2

Open Time      Open      High       Low     Close      Volume  \
0      1601510400000  10776.59  10786.88  10776.59  10781.13   71.839045   
1      1601510460000  10781.02  10799.90  10779.87  10796.00  149.010542   
2      1601510520000  10796.00  10796.00  10791.50  10791.50   41.615967   
3      1601510580000  10791.51  10799.00  10791.50  10798.90   41.856550   
4      1601510640000  10798.90  10826.19  10798.80  10811.29  232.593454   
...              ...       ...       ...       ...       ...         ...   
43196  1604102160000  13543.20  13556.52  13535.05  13542.35   40.031404   
43197  1604102220000  13542.35  13560.51  13542.35  13557.51   20.064288   
43198  1604102280000  13557.51  13559.02  13545.88  13548.86   27.444955   
43199  1604102340000  13548.86  13560.12  13546.35  13560.10   19.307425   
43200  1604102400000  13560.10  13568.08  13560.10  13567.33   19.207796   

          Close Time           QAV   NOT       TBBAV         TBQAV  U  
0      1601510459999  7.745923e+05  1035   35.352141  3.811842e+05  0  
1      1601510519999  1.608254e+06  1496   96.678226  1.043326e+06  0  
2      1601510579999  4.491854e+05   368   14.347543  1.548601e+05  0  
3      1601510639999  4.519085e+05   520   18.872538  2.037320e+05  0  
4      1601510699999  2.515244e+06  2069  164.605071  1.779825e+06  0  
...              ...           ...   ...         ...           ... ..  
43196  1604102219999  5.422165e+05   774    9.959911  1.349007e+05  0  
43197  1604102279999  2.719363e+05   572   10.983299  1.488713e+05  0  
43198  1604102339999  3.719431e+05   953   14.799719  2.005764e+05  0  
43199  1604102399999  2.616939e+05   927   10.997008  1.490504e+05  0  
43200  1604102459999  2.605286e+05   560   14.254550  1.933420e+05  0  

[43201 rows x 12 columns]

In [9]:
#--- remove first row
df3 = df2.iloc[1: , :]

end_it=int(len(df3.Open)/60)
end_it

#--- number of iterations in df per minutes/hrs
iterator=np.arange(1,end_it+1,1)
#iterator

In [10]:
#--------------------------------------------------------------------------------------------------------------------------
#----- This piece of code transform the data in df2 and produces a list 'data2' with the same structure as the 'data' list
#--------------------------------------------------------------------------------------------------------------------------

data2=[]
for idx, elements in enumerate(iterator):
    aux_data=[]
    end_=60*(idx+1)
    #print(idx+1)
    
    if idx==0:
        starter=1
        #print(df3[starter-1:end_])
        aux=df3[starter-1:end_]
    else:    
        starter=end_-60
        #print(df3[starter-1:end_])
        aux=df3[starter-1:end_]
        
    for idx2, elem2 in enumerate(aux.Open):
        rows=aux[aux['Open']==elem2]
        #print('Im row: ',rows)
        Open_Time,Open,High,Low,Close,Volume=np.array(rows['Open Time'])[0],np.array(rows.Open)[0],np.array(rows.High)[0],np.array(rows.Low)[0],np.array(rows.Close)[0],np.array(rows.Volume)[0]
        #Open Time / Open/High/Low /Close/ Volume
        OP_time=int(Open_Time/1000)
        #print(OP_time)
        feature_list=[OP_time,Open,High,Low,Close,Volume]
        aux_data.append(feature_list)
        
    data2.append(aux_data)    
    #print(starter)
    #print(end_)
    #print('iteration ended')


In [11]:
data2

[[[1601510460, 10781.02, 10799.9, 10779.87, 10796.0, 149.010542],
  [1601510520, 10796.0, 10796.0, 10791.5, 10791.5, 41.615967],
  [1601510580, 10791.51, 10799.0, 10791.5, 10798.9, 41.85655],
  [1601510640, 10798.9, 10826.19, 10798.8, 10811.29, 232.593454],
  [1601510700, 10811.29, 10822.33, 10811.29, 10821.23, 65.696265],
  [1601510760, 10821.22, 10825.16, 10814.85, 10814.97, 54.83685],
  [1601510820, 10814.97, 10816.27, 10808.22, 10812.2, 58.478283],
  [1601510880, 10812.2, 10821.07, 10808.42, 10820.61, 54.60173],
  [1601510940, 10820.6, 10821.51, 10812.83, 10812.83, 51.730053],
  [1601511000, 10812.84, 10816.17, 10808.23, 10809.49, 48.728149],
  [1601511060, 10809.49, 10810.19, 10807.73, 10807.78, 35.454644],
  [1601511120, 10807.78, 10811.16, 10805.88, 10810.7, 45.125631],
  [1601511180, 10810.7, 10811.52, 10805.48, 10808.46, 92.229904],
  [1601511240, 10808.46, 10810.19, 10806.79, 10807.29, 30.707182],
  [1601511300, 10807.29, 10815.74, 10807.29, 10814.32, 38.370826],
  [160151136

#### Use createTrainTestSets with this new list data2 

In [12]:
#data = json.load(f)

total2 = []
for i in data2:
    for j in i:
        time = pd.to_datetime(j[0], unit='s')
        open_ = j[1]
        high = j[2]
        low = j[3]
        close = j[4]
        vol = j[5]
        total2.append( [time, open_, high, low, close, vol])

In [13]:
# dataset.createTrainTestSets(COIN_PAIR, data, training_window=TRAINING_WINDOW, labeling_window=LABELING_WINDOW)
time_list, x, y, prices = createTrainTestSets(total2, training_window = 20, labeling_window = 60, feature_window = 30)

> Finished Creating set - Size:  730   730  P:  403  N:  327


In [14]:
#---- compare output with result from line 64 of Controller.py: 
# x_train, y_train, _ = dataset.createTrainTestSets(COIN_PAIR, data, training_window=TRAINING_WINDOW, labeling_window=LABELING_WINDOW)
print(len(x),len(x[0]))
x,y

730 12


(array([[-0.56177048,  1.22621174,  1.22235168, ...,  0.        ,
         -1.36755403, -1.28135761],
        [-0.45096725,  1.28949491,  1.28874133, ...,  0.        ,
         -0.11284262, -0.11025022],
        [-0.29175489, -0.25074501, -0.2476725 , ...,  0.        ,
         -0.41225494, -0.43848954],
        ...,
        [-0.31320304, -1.08515702, -1.08159253, ...,  0.        ,
          0.36169146,  0.41081545],
        [ 0.14179444,  1.72988563,  1.72491603, ...,  0.        ,
         -1.66696635, -1.50123906],
        [ 0.18034114, -0.82347845, -0.82357954, ...,  0.        ,
          0.53418968,  0.59303857]]),
 array([0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 0, 0,
        0, 1, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1,
        0, 0, 0, 1, 1, 0, 0, 1, 0, 1, 1, 1, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0,
        0, 1, 0, 1, 1, 0, 0, 0, 0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 0, 0, 0, 0,
        0, 0, 1, 1, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0,
   

#### Can we use this as it is and feed into the DNN model?

In [15]:
import pandas as pd 
import numpy as np
import os
import matplotlib.pyplot as plt
from collections import deque
import random

from sklearn import preprocessing
from sklearn.preprocessing import OneHotEncoder as encoder
from sklearn.model_selection import train_test_split

import tensorflow as tf
from tensorflow.keras.models import load_model
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout, BatchNormalization, Flatten
from tensorflow.keras.optimizers import RMSprop
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.callbacks import TensorBoard, ModelCheckpoint

np.warnings.filterwarnings('ignore')
pd.set_option('display.max_columns', 10)
cwd = os.path.dirname(os.getcwd())

In [16]:
#--- this is just for now...
X_train, y_train = x,y #preprocess_train_df(train_df, SEQUENCE_LEN)
X_val, y_val = x,y     #preprocess_test_df(val_df, SEQUENCE_LEN)

#----------- MODEL VARS --------------------------#
FUTURE_PERIOD = 1
#EPOCHS = 20
BATCH_SIZE = 50

In [17]:
# DNN MODEL AIMENDEZ:

"""
model = Sequential()

model.add(LSTM(256, input_shape = (X_train.shape[1:]), return_sequences=True  ))
model.add(Dropout(0.35))
model.add(BatchNormalization())

model.add(LSTM(32))
model.add(Dropout(0.35))
model.add(BatchNormalization())

model.add(Dense(100, activation = 'relu'))
model.add(Dropout(0.35))

model.add(Dense(30, activation = 'relu'))

model.add(Dense(1, activation = 'sigmoid'))

"""

"\nmodel = Sequential()\n\nmodel.add(LSTM(256, input_shape = (X_train.shape[1:]), return_sequences=True  ))\nmodel.add(Dropout(0.35))\nmodel.add(BatchNormalization())\n\nmodel.add(LSTM(32))\nmodel.add(Dropout(0.35))\nmodel.add(BatchNormalization())\n\nmodel.add(Dense(100, activation = 'relu'))\nmodel.add(Dropout(0.35))\n\nmodel.add(Dense(30, activation = 'relu'))\n\nmodel.add(Dense(1, activation = 'sigmoid'))\n\n"

In [18]:
X_train.shape[1:],np.shape(X_train)

((12,), (730, 12))

In [19]:
#--- Next try: use code from Model.py

    
model = Sequential()


X_train = X_train.reshape(-1,1,len(X_train[0]))
x = len(X_train[0])

model.add(LSTM(256,input_shape=((1,x)), return_sequences = True, activation = "relu"))
model.add(Dropout(0.2))
model.add(BatchNormalization())

model.add(LSTM(128, input_shape=((1, x)), return_sequences=True, activation="relu"))
model.add(Dropout(0.2))
model.add(BatchNormalization())

model.add(LSTM(128, input_shape=((1, x)), activation="relu"))
model.add(Dropout(0.2))
model.add(BatchNormalization())

model.add(Dense(32, activation="relu"))
model.add(Dropout(0.2))

model.add(Dense(2, activation="softmax"))            

In [20]:
optimizer = tf.keras.optimizers.Adam(lr = 0.001, decay = 1e-6)
model.compile(loss="sparse_categorical_crossentropy",optimizer=optimizer)

In [21]:
BATCH_SIZE = 50
#FIT 
history = model.fit(X_train, y_train, batch_size = BATCH_SIZE, epochs = 100, validation_data = (X_val, y_val), verbose= 1)

Epoch 1/100


ValueError: in user code:

    C:\Users\vicmual\AppData\Roaming\Python\Python38\site-packages\tensorflow\python\keras\engine\training.py:855 train_function  *
        return step_function(self, iterator)
    C:\Users\vicmual\AppData\Roaming\Python\Python38\site-packages\tensorflow\python\keras\engine\training.py:845 step_function  **
        outputs = model.distribute_strategy.run(run_step, args=(data,))
    C:\Users\vicmual\AppData\Roaming\Python\Python38\site-packages\tensorflow\python\distribute\distribute_lib.py:1285 run
        return self._extended.call_for_each_replica(fn, args=args, kwargs=kwargs)
    C:\Users\vicmual\AppData\Roaming\Python\Python38\site-packages\tensorflow\python\distribute\distribute_lib.py:2833 call_for_each_replica
        return self._call_for_each_replica(fn, args, kwargs)
    C:\Users\vicmual\AppData\Roaming\Python\Python38\site-packages\tensorflow\python\distribute\distribute_lib.py:3608 _call_for_each_replica
        return fn(*args, **kwargs)
    C:\U